In [519]:
from Bio import SeqIO
from Bio.SeqRecord import SeqRecord
from Bio.Seq import Seq
import numpy as np
import random
import csv
import string

In [576]:
#inputs
# specify an input single-entry-fasta or text file containing a read structure
single_input_fasta = "/Users/pracheetishikarkhane/Documents/test_sim_script/VVV/VVV.fasta"

# specify an input fasta file with anywhere between 1 to 30 unique barcode
multi_input_fasta = "/Users/pracheetishikarkhane/Documents/ngs_sim_data/barcodeLookup/3barcodes.fasta"

# specify read seqeunce for testing purposes:
#read_sequence = "AATGATACGGCGACCACCGAGATCTACACTCTTTCCCTACACGACGCTCTTCCGATCTCCCTCCCTCTTTCTTTCCCTCCTCCTCCTCCATGGAGATCGGAAGAGCACACGTCTGAACTCCAGTCACATCACGATCTCGTATGCCGTCTTCTGCTTG"
csv_file = "/Users/pracheetishikarkhane/Documents/sim.csv"
num_reads = 20000
output_folder = "/Users/pracheetishikarkhane/Documents/test_sim_script/test_ONT"
sequencing_type = "ONT"
sample_name = "VVV"
# optional argument 
#output_seq

# read in sequence from file
with open(single_input_fasta, "r") as handle:
    for record in SeqIO.parse(handle, "fasta"):
        read_sequence = str(record.seq)

print(read_sequence)

CCCTCCCTCTTTCTTTCCCTCCCTCCCTCTCCCTCCCTCCCTCTCCCTCCCTCCCTCTCCCTCCATGGAGATCGGAAGAGCACACGTCTGAACTCCAGTCACATCACGATCTCGTATGCCGTCTTCTGCTTG


In [577]:
# read parameters from csv file
parameters = {}

with open(csv_file, newline='') as csvfile:
    csv_reader = csv.reader(csvfile)
    for row in csv_reader:
        parameter_name = row[0]
        parameter_values = row[1:]
        parameters[parameter_name] = parameter_values

# Now you have the parameters in a dictionary where the parameter name is the key and the values are stored as a list.
# For example:
#print(parameters['insertionFrequency'])  # Output: ['1e-6', '1e-6', '1e-6', '1e-6']
#print(parameters['qScoreMedian'])


insertion_freq = int_list = list(map(float, parameters['insertionFrequency']))
deletion_freq = list(map(float, parameters['deletionFrequency']))

substitution_freq_R1 = list(map(float, parameters['substitutionFrequencyR1']))
substitution_freq_R2 = list(map(float, parameters['substitutionFrequencyR2']))

substitution_bias_R1 = list(map(int, parameters['substitutionBiasR1']))
print(substitution_bias_R1)
substitution_bias_R2 = list(map(int, parameters['substitutionBiasR2']))

q_score_lower_quartile = list(map(int, parameters['qScoreLowerQuartile']))
q_score_median = list(map(int, parameters['qScoreMedian']))
q_score_upper_quartile = list(map(int, parameters['qScoreUpperQuartile']))

substitution_q_score_lower_quartile_R1 = list(map(int, parameters['substitutionQScoreLowerQuartileR1']))
substitution_q_score_median_R1 = list(map(int, parameters['substitutionQScoreMedianR1']))
substitution_q_score_upper_quartile_R1 = list(map(int, parameters['substitutionQScoreUpperQuartileR1']))

substitution_q_score_lower_quartile_R2 = list(map(int, parameters['substitutionQScoreLowerQuartileR2']))
substitution_q_score_median_R2 = list(map(int, parameters['substitutionQScoreMedianR2']))
substitution_q_score_upper_quartile_R2 = list(map(int, parameters['substitutionQScoreUpperQuartileR2']))

indel_q_score_lower_quartile_R1R2 = list(map(int, parameters['indelQScoreLowerQuartileR1R2']))
indel_q_score_median_R1R2 = list(map(int, parameters['indelQScoreMedianR1R2']))
indel_q_score_upper_quartile_R1R2 = int_list = list(map(int, parameters['indelQScoreUpperQuartileR1R2']))

print(indel_q_score_upper_quartile_R1R2)

[3, 2, 2, 3]
[39, 39, 38, 39]


In [578]:
# RUNNING INTO ERRORS WRITING INTO FASTQ
def write_fastq_records(records):
    if sequencing_type == "MiSeq":
        
        r1_records = [rec for i, rec in enumerate(records) if i % 2 == 0]
        r2_records = [rec for i, rec in enumerate(records) if i % 2 == 1]
        
        r1_file = f"{output_folder}/R1.fastq"
        r2_file = f"{output_folder}/R2.fastq"

        # need to specify r1_records and r2_records
        with open(r1_file, "w") as handle:
            SeqIO.write(r1_records, handle, "fastq")

        with open(r2_file, "w") as handle:
            SeqIO.write(r2_records, handle, "fastq")
            
        #with open(output_file, "w") as handle:
        #    SeqIO.write(records, handle, "fastq")
        
    elif sequencing_type == "ONT":
        # Combine R1 and R2 reads for ONT
        combined_records = records

        combined_file = f"{output_folder}/combined.fastq"

        with open(combined_file, "w") as handle:
            SeqIO.write(combined_records, handle, "fastq")
            

In [579]:
def check_accuracy(num_modifications, seq_length):
    # return True if desired accuracy is not yet met, return False otherwise
    # desired accuracy for MiSeq is ~99.99%
    # desired accuracy for ONT is ~95%
    
    if sequencing_type == "MiSeq":
        accuracy = (seq_length - num_modifications) * 100 / seq_length
        print(accuracy)
        if (accuracy >= 99.0) and (accuracy < 100.0):
            print("i am true")
            return False
        
    elif sequencing_type == "ONT":
        accuracy = (seq_length - num_modifications) * 100 / seq_length
        if (accuracy > 94.0) and (accuracy < 96.0):
            return False
    
    return True

In [597]:
def apply_sequencing_errors(read_sequence, insertion_freq, deletion_freq, substitution_freq, substitution_bias,
                            q_score_median, q_score_lower_quartile, q_score_upper_quartile,
                            substitution_q_score_median, substitution_q_score_lower_quartile, substitution_q_score_upper_quartile,
                            indel_q_score_median, indel_q_score_lower_quartile, indel_q_score_upper_quartile):
    
    # Convert the read sequence to a list for easier manipulation
    sequence_list = list(read_sequence)
    seq_length = len(sequence_list)
    num_modifications = 0

    # using qScoreMedian, qScoreLowerQuartile, and qScoreUpperQuartile
    # Assign random q score to each base
    q_scores = [random.randint(q_score_lower_quartile[0], q_score_upper_quartile[0]) for _ in range(seq_length)]
    
    print(seq_length)
    print(len(q_scores))

    # Apply random insertions
    insertion_freq_arr = [seq_length * insertion_freq[0], seq_length * insertion_freq[0], 
                          seq_length * insertion_freq[0], seq_length * insertion_freq[0]]
    bases = ["A", "C", "G", "T"]
    num_insertions = random.randint(seq_length // 4, seq_length // 2) # may need to change this
    base = ""
    base_pos = 0
    
    for _ in range(num_insertions):
        random_array = np.random.rand(4)
        # choose which base to insert based on this comparison, could also have randomly picked a base
        for i in range(len(insertion_freq_arr)):
            if insertion_freq_arr[i] > random_array[i]:
                base = bases[i]
                base_pos = i
                break
            
        if (base != ""):
            print("added a base")
            position = random.randint(0, seq_length)
            sequence_list.insert(position, base)
            q_scores.insert(position, random.randint(indel_q_score_lower_quartile[base_pos], indel_q_score_upper_quartile[base_pos]))
            seq_length += 1
            base = ""
            num_modifications += 1
        
        if sequencing_type == "MiSeq" and num_modifications == 1:
            break


    # Apply random deletions
    base = ""
    counts_arr = [sequence_list.count(base) for base in bases]
    deletion_freq_arr = [deletion_freq[i] * counts_arr[i] for i in range(len(counts_arr))]
    num_deletions = random.randint(seq_length // 4, seq_length // 2) # may need to change this
    base_pos = 0
    
    for _ in range(num_deletions):
        random_array = np.random.rand(4)
        for i in range(len(deletion_freq_arr)):
            if deletion_freq_arr[i] > random_array[i]:
                base = bases[i]
                base_pos = i
                break
        
        if sequencing_type == "MiSeq" and num_modifications == 1:
            break
            
        # overhead to find random position of a specified base, can just delete at a random position instead
        if (base != ""):
            print("deleted a base")
            positions = [pos for pos, char in enumerate(sequence_list) if char == base]
            
            if 0 in positions:
                positions.remove(0)
                
            random_position = random.choice(positions)
            del sequence_list[random_position]
            # this base pos might be long
            del q_scores[random_position]
            q_scores[random_position - 1] = random.randint(indel_q_score_lower_quartile[base_pos], indel_q_score_upper_quartile[base_pos])
            seq_length -= 1
            base = ""
            num_modifications += 1
          
       
    
    # Apply random substitutions
    base = ""
    num_substitutions = random.randint(seq_length // 4, seq_length // 2)
    substitution_freq_arr = [substitution_freq[i] * counts_arr[i] for i in range(len(counts_arr))] # [25, 25, 25, 25] * [1e-3, 1e-3, 1e-3, 1e-3] = [25e-3, 25e-3, 25e-3, 25e-3]
    new_sub_bias = list(substitution_bias)
    possible_substitution_bases = list(bases)
    
    for _ in range(num_substitutions):
        random_array = np.random.rand(4) # randomly generate 1 by 4 array within [0, 1] space
        for i in range(len(substitution_freq_arr)):
            if substitution_freq_arr[i] > random_array[i]:
                base = bases[i] # choose base to remove
                base_pos = i
                del new_sub_bias[i] # [3, 2, 3]
                del possible_substitution_bases[i] # if C was chosen as base to remove, substitution bases will be A, G, T
                
                break
        
        if sequencing_type == "MiSeq" and num_modifications == 1:
            break
            
        if (base != ""):
        # delete a random selected base
            print("substituted a base")
            positions = [pos for pos, char in enumerate(sequence_list) if char == base] # find all positions of selected base
            random_position = random.choice(positions) # select a random one of those positions
            del sequence_list[random_position] # delete that base from the sequence

            sum_probability = sum(new_sub_bias) # find sum of the substitution biases
            sub_bases_probabilities = [probability / sum_probability for probability in new_sub_bias] # probability of A, G, T = [3, 2, 3] / sum ([3, 2, 3]) = [0.375, 0.25, 0.375]
            cumulative_probability_distribution = [sub_bases_probabilities[0], 
                                                   sub_bases_probabilities[0] + sub_bases_probabilities[1],
                                                   sub_bases_probabilities[0] + sub_bases_probabilities[1] + sub_bases_probabilities[2]] # cumulative probability distribution = [0.375, 0.625, 1]

            random_number = random.random() # randomly generate number between 0 and 1 
            # determine new base to replace the old base with
            if random_number < cumulative_probability_distribution[0]:
                new_base = possible_substitution_bases[0]
            elif random_number < cumulative_probability_distribution[1]:
                new_base = possible_substitution_bases[1]
            else:
                new_base = possible_substitution_bases[2]

            sequence_list.insert(random_position, new_base)
            q_scores[random_position] = random.randint(substitution_q_score_lower_quartile[base_pos], substitution_q_score_upper_quartile[base_pos])
            
            # restore substitution bias and possible bases to substitute with
            new_sub_bias = list(substitution_bias)
            possible_substitution_bases = list(bases)
            base = ""
            num_modifications += 1

    # Convert the list back to a string sequence
    seq_with_errors = "".join(sequence_list)

    print("Seq_len:" + str(seq_length))
    print("Q-score:" + str(len(q_scores)))
    return seq_with_errors, q_scores
    

In [598]:
def generate_random_ID():
    characters = string.ascii_letters + string.digits
    rand_16 = ''.join(random.choice(characters) for _ in range(16))
    return (sample_name + rand_16)

In [599]:
def main():
    synthetic_reads = []
    for _ in range(num_reads // 2):
        synthetic_read_1, R1_q_scores = apply_sequencing_errors(read_sequence, insertion_freq, deletion_freq,
                                                       substitution_freq_R1, substitution_bias_R1,
                                                       q_score_median, q_score_lower_quartile, q_score_upper_quartile,
                                                       substitution_q_score_median_R1, substitution_q_score_lower_quartile_R1, substitution_q_score_upper_quartile_R1,
                                                       indel_q_score_median_R1R2, indel_q_score_lower_quartile_R1R2, indel_q_score_upper_quartile_R1R2)
        synthetic_read_2, R2_q_scores = apply_sequencing_errors(read_sequence, insertion_freq, deletion_freq,
                                                       substitution_freq_R2, substitution_bias_R2,
                                                       q_score_median, q_score_lower_quartile, q_score_upper_quartile,
                                                       substitution_q_score_median_R2, substitution_q_score_lower_quartile_R2, substitution_q_score_upper_quartile_R2,
                                                       indel_q_score_median_R1R2, indel_q_score_lower_quartile_R1R2, indel_q_score_upper_quartile_R1R2)
        
        record1 = SeqRecord(Seq(synthetic_read_1))
        record2 = SeqRecord(Seq(synthetic_read_2))
        
        record1.letter_annotations["phred_quality"] = R1_q_scores
        record2.letter_annotations["phred_quality"] = R2_q_scores
        
        synthetic_reads.append(record1)
        synthetic_reads.append(record2)
        
        record1.id = generate_random_ID()
        record2.id = generate_random_ID()
        
    
    # add code to insert barcode 
    write_fastq_records(synthetic_reads)
    print("completed")

In [600]:
main()

132
132
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:

substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-sc

substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substitute

substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
added a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:133
Q-score:133
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:13

substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
subs

...

substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:133
Q-score:133
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
added a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:133
Q-score:133
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a ba

substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substitute

substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substitute

substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
added a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:133
Q-score:133
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
Seq_len:132
Q-score:132
132
132
substituted a base
substituted a base
substituted a base
substituted a base
substituted a base
substituted a ba

completed
